# Finetuning Gemma 3 1B with QLoRA for Text-to-SQL on Local Machine

This Jupyter notebook provides a comprehensive guide to finetune the Gemma 3 1B model using Quantized Low-Rank Adaptation (QLoRA) on the `gretelai/synthetic_text_to_sql` dataset. The process is designed to be executed on a local machine with GPU support.

## Table of Contents

1.  **Introduction**
2.  **Setup and Installation**
3.  **Model Loading and QLoRA Configuration**
4.  **Dataset Preparation**
5.  **Training the Model**
6.  **Saving the Finetuned Model**
7.  **Inference and Evaluation (Optional)**

## 1. Introduction

Large Language Models (LLMs) have shown remarkable capabilities across various natural language processing tasks. However, finetuning these models for specific downstream tasks often requires significant computational resources. QLoRA is an efficient finetuning technique that reduces memory usage while maintaining performance, making it feasible to finetune large models on consumer-grade GPUs.

This notebook focuses on adapting Gemma 3 1B, a powerful open-source model, to generate SQL queries from natural language prompts and database schemas. The `gretelai/synthetic_text_to_sql` dataset provides a rich collection of synthetic text-to-SQL examples, ideal for this task.


## 2. Setup and Installation

Before proceeding, ensure you have a suitable Python environment (Python 3.9+) and a GPU with sufficient memory (at least 12GB recommended for Gemma 3 1B). We will install the necessary libraries, including `unsloth`, `bitsandbytes`, `accelerate`, `peft`, `trl`, and `datasets`.

**Note**: The `unsloth` library provides optimized implementations for finetuning, significantly speeding up the process. It handles patching of various components for better performance.


In [1]:
# Install necessary libraries
!pip install --no-deps bitsandbytes accelerate xformers==0.0.29.post3 peft trl triton cut_cross_entropy unsloth_zoo
!pip install sentencepiece protobuf "datasets>=3.4.1" huggingface_hub hf_transfer
!pip install --no-deps unsloth

# Verify installation (optional)
try:
    import unsloth
    print("Unsloth installed successfully!")
except ImportError:
    print("Unsloth installation failed. Please check your environment.")


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.4/43.4 MB 19.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.0/67.0 MB 11.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 375.8/375.8 kB 31.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.4/152.4 kB 15.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.5/491.5 kB 29.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 kB 19.4 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2025.3.2
    Uninstalling fsspec-2025.3.2:
      Successfully uninstalled fsspec-2025.3.2
  Attempting uninstall: datasets
    Found existing installation: datasets 2.14.4
    Uninstalling datasets-2.14.4:
      Successfully uninstalled datasets-2.14.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
unsloth-zoo 2025.6.

## 3. Model Loading and QLoRA Configuration

We will load the Gemma 3 1B model and configure it for QLoRA finetuning using `unsloth.FastModel`. This involves specifying the base model, the LoRA parameters (rank, alpha, dropout), and which layers to finetune.


In [3]:
import torch
from unsloth import FastLanguageModel

max_seq_length = 2048 # You can set this to 8192 for Gemma 3 8B
dtype = None # None for auto detection. Supports torch.float16, torch.bfloat16, torch.float32
load_in_4bit = True # Use 4bit quantization to save memory

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "google/gemma-3-1b-it",
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
    # token = "hf_xxxxxxxxxxxxxxxxxxxxxxxxxxxx" # Use this if you want to use a private model
)

model = FastLanguageModel.get_peft_model(
    model,
    r = 16, # LoRA rank. Higher rank means more parameters, potentially better performance but more memory.
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj"],
    lora_alpha = 16, # LoRA alpha. Recommended to be equal to r.
    lora_dropout = 0.05,
    bias = "none",
    use_gradient_checkpointing = "unsloth", # Recommended for memory efficiency
    random_state = 3407,
    use_rslora = False, # Rank-Stabilized LoRA. Set to True for larger models.
    loftq_config = None, # LoFTQ configuration. Not used here.
)


==((====))==  Unsloth 2025.6.5: Fast Gemma3 patching. Transformers: 4.52.4.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 7.5. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: Using float16 precision for gemma3 won't work! Using float32.
Unsloth: Making `model.base_model.model.model` require gradients


## 4. Dataset Preparation

We will load the `gretelai/synthetic_text_to_sql` dataset from Hugging Face. The dataset needs to be transformed into a conversational format suitable for finetuning. We will create a `conversations` field, where each conversation is a list of turns between a 'user' and an 'assistant'.

The prompt structure will be:

```
Given the following database schema:
{sql_context}

Generate the SQL query for: {sql_prompt}
```

And the assistant's response will be the `sql` query.


In [6]:
from datasets import load_dataset

# Load the dataset
dataset = load_dataset("gretelai/synthetic_text_to_sql", split = "train")

# Define the formatting function
def formatting_prompts_func(examples):
    inputs = []
    for i in range(len(examples["sql_prompt"])):
        user_message = f'''Given the following database schema:
\n{examples["sql_context"][i]}\n\nGenerate the SQL query for: {examples["sql_prompt"][i]}'''
        assistant_message = examples["sql"][i]
        inputs.append([
            {"role": "user", "content": user_message},
            {"role": "assistant", "content": assistant_message}
        ])
    return {"conversations": inputs}

# Apply the formatting function to the dataset
dataset = dataset.map(formatting_prompts_func, batched = True)

# Apply chat template and remove <bos> token
def apply_chat_template(examples):
    texts = []
    for convo in examples["conversations"]:
        text = tokenizer.apply_chat_template(convo, tokenize=False, add_generation_prompt=False)
        texts.append(text.removeprefix("<bos>")) # Remove <bos> as the processor will add it
    return {"text": texts}

dataset = dataset.map(apply_chat_template, batched=True)

# Print an example to verify
print("Example of processed data:")
print(dataset[0]["text"])


Generating train split:   0%|          | 0/100000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/5851 [00:00<?, ? examples/s]

Map:   0%|          | 0/100000 [00:00<?, ? examples/s]

Map:   0%|          | 0/100000 [00:00<?, ? examples/s]

Example of processed data:
<start_of_turn>user
Given the following database schema:

CREATE TABLE salesperson (salesperson_id INT, name TEXT, region TEXT); INSERT INTO salesperson (salesperson_id, name, region) VALUES (1, 'John Doe', 'North'), (2, 'Jane Smith', 'South'); CREATE TABLE timber_sales (sales_id INT, salesperson_id INT, volume REAL, sale_date DATE); INSERT INTO timber_sales (sales_id, salesperson_id, volume, sale_date) VALUES (1, 1, 120, '2021-01-01'), (2, 1, 150, '2021-02-01'), (3, 2, 180, '2021-01-01');

Generate the SQL query for: What is the total volume of timber sold by each salesperson, sorted by salesperson?<end_of_turn>
<start_of_turn>model
SELECT salesperson_id, name, SUM(volume) as total_volume FROM timber_sales JOIN salesperson ON timber_sales.salesperson_id = salesperson.salesperson_id GROUP BY salesperson_id, name ORDER BY total_volume DESC;<end_of_turn>



## 5. Training the Model

We will use the `SFTTrainer` from the `trl` library to train the model. This trainer simplifies the finetuning process for causal language models. We will configure the training arguments such as batch size, learning rate, and number of training steps.


In [7]:
from trl import SFTTrainer
from transformers import TrainingArguments

# Define training arguments
training_args = TrainingArguments(
    per_device_train_batch_size = 2,
    gradient_accumulation_steps = 4,
    warmup_steps = 5,
    max_steps = 100, # Adjust as needed. Set to -1 for full dataset training.
    learning_rate = 2e-4,
    fp16 = not torch.cuda.is_bf16_supported(), # Use fp16 if bfloat16 is not supported
    bf16 = torch.cuda.is_bf16_supported(), # Use bfloat16 if supported
    logging_steps = 1,
    output_dir = "outputs",
    optim = "adamw_8bit",
    seed = 3407,
    # num_train_epochs = 1, # Uncomment for full epoch training
    # push_to_hub = True, # Uncomment to push to Hugging Face Hub
    # hub_model_id = "your_hf_username/gemma-3-1b-text-to-sql",
    # hub_token = "hf_xxxxxxxxxxxxxxxxxxxxxxxxxxxx",
)

# Initialize SFTTrainer
trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset,
    dataset_text_field = "text",
    args = training_args,
)

# Start training
trainer.train()


Unsloth: Switching to float32 training since model cannot work with float16


Unsloth: Tokenizing ["text"]:   0%|          | 0/100000 [00:00<?, ? examples/s]

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 100,000 | Num Epochs = 1 | Total steps = 100
O^O/ \_/ \    Batch size per device = 2 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (2 x 4 x 1) = 8
 "-____-"     Trainable parameters = 13,045,760/1,000,000,000 (1.30% trained)
wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize?ref=models
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: duy682005zac (duy682005zac-hanoi-university-of-science) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.


wandb: WARNING The get_url method is deprecated and will be removed in a future release. Please use `run.url` instead.


TrainOutput(global_step=100, training_loss=0.8965935689210892, metrics={'train_runtime': 474.021, 'train_samples_per_second': 1.688, 'train_steps_per_second': 0.211, 'total_flos': 707244926515200.0, 'train_loss': 0.8965935689210892})

## 6. Saving the Finetuned Model

After training, we will save the finetuned model. The `save_pretrained_merged` function from `unsloth` allows saving the LoRA adapters merged with the base model, creating a standalone finetuned model.


In [8]:
# Save the finetuned model
model.save_pretrained_merged("gemma_3_1b_text_to_sql_finetuned", tokenizer, save_method = "merged_16bit")

# You can also save in 4bit or other formats
# model.save_pretrained_merged("gemma_3_1b_text_to_sql_finetuned_4bit", tokenizer, save_method = "merged_4bit")


Found HuggingFace hub cache directory: /root/.cache/huggingface/hub
Checking cache directory for required files...
Cache check failed: model.safetensors not found in local cache.
Not all required files found in cache. Will proceed with downloading.


Unsloth: Merging weights into 16bit: 100%|██████████| 1/1 [01:45<00:00, 105.73s/it]


## 7. Inference and Evaluation (Optional)

This section demonstrates how to load the finetuned model and perform inference. You can also add code here to evaluate the model's performance on a test set.


In [14]:
# Load the finetuned model for inference
from unsloth import FastLanguageModel

model, tokenizer = FastLanguageModel.from_pretrained(
    model_name = "gemma_3_1b_text_to_sql_finetuned",  # Path to your saved model
    max_seq_length = max_seq_length,
    dtype = dtype,
    load_in_4bit = load_in_4bit,
)

# Example prompt as a chat-style conversation
conversation = [
    {
        "role": "user",
        "content": (
            "Given the following database schema:\n"
            "CREATE TABLE Employees (id INT, name VARCHAR(255), salary INT);\n\n"
            "Generate the SQL query for: Select all employees with salary greater than 50000"
        )
    }
]

# Apply chat template
prompt = tokenizer.apply_chat_template(conversation, tokenize=False, add_generation_prompt=True)

# Tokenize and move to device
inputs = tokenizer([prompt], return_tensors="pt").to("cuda")

# Generate
outputs = model.generate(**inputs, max_new_tokens=128, use_cache=True)
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

==((====))==  Unsloth 2025.6.5: Fast Gemma3 patching. Transformers: 4.52.4.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.6.0+cu124. CUDA: 7.5. CUDA Toolkit: 12.4. Triton: 3.2.0
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.29.post3. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: Using float16 precision for gemma3 won't work! Using float32.
user
Given the following database schema:
CREATE TABLE Employees (id INT, name VARCHAR(255), salary INT);

Generate the SQL query for: Select all employees with salary greater than 50000
model
SELECT name, salary FROM Employees WHERE salary > 50000;
